# Домашнее задание 3
## Сравнение интересов аудитории телеканалов НТВ и Дождь с помощью тематического моделирования LDA

Задача:
Сравнить интересы аудитории телеканолов НТВ и Дождь с помощью методов тематического моделирования
1. Получить данные по аудитории из социальной сети ВК
2. Зарегистрировать приложение, получить app_id, access_token
3. Скачать данные по пользователям в каждой из групп (id групп ВК даны ниже, tvrain_id, ntv_id)
4. Взять небольшую выборку из каждой совокупности телезрителей(около 1000-2000 человек, т.к. 300k-400k слишком много), с которыми работать дальше
5. Обучить LDA модель на их подписках
6. По группам, на которые подписаны эти люди, полуичть ключевые слова групп, на которые они подписаны
7. Получить распределение интересов людей для каждой совокупности, сравнить на графике

In [1]:
import seaborn as sb
import sys  
import pandas as pd
import requests
import numpy as np
import datetime
import time
import pickle
import matplotlib.pyplot as plt
import time
%matplotlib inline

from bs4 import BeautifulSoup as bs
import urllib

In [2]:
def load_obj(name):
    with open(name + '.pkl', 'rb') as f:
        return pickle.load(f)

def save_obj(obj, name):
    with open(name + '.pkl', 'wb') as f:
        pickle.dump(obj, f, pickle.HIGHEST_PROTOCOL)

#### Для использования VK API необходимо создать приложение в VK

1. Создать приложение по адресу https://vk.com/apps?act=manage (кнопка "создать приложение")
2. При создании указать название, описание (можно любые), категория  - прочее. Тип - standalone приложение
3. В настройках получить **app_id**. App_id потребуется для получения access token
4. Авторизовать пользователя (получить access token) можно по адресу: https://vk.com/dev/first_guide, в правилах нас интересует пункт 3 **Авторизация пользователя**
5. После того, как ознакомитесь с авторизацией пользователя, скопируйте в адресную строку такой запрос https://oauth.vk.com/authorize?client_id=5490057&display=page&redirect_uri=https://oauth.vk.com/blank.html&scope=friends&response_type=token&v=5.52, где число **5490057** замените на число, которое получите для вашего **app_id**
6. Нажмите Enter. Откроется окно с запросом прав. В нем отображаются название приложения, иконки прав доступа, и Ваши имя с фамилией. Нажмите «Разрешить». Вы попадете на новую страницу с предупреждением о том, что токен нельзя копировать и передавать третьим лицам. В адресной строке будет URL https://oauth.vk.com/blank.html, а после # Вы увидите дополнительные параметры — access_token, expires_in и user_id. Токен может выглядеть, например, так: 51eff86578a3bbbcb5c7043a122a69fd04dca057ac821dd7afd7c2d8e35b60172d45a26599c08034cc40a
7. Токен — это Ваш ключ доступа. При выполнении определенных условий человек, получивший Ваш токен, может нанести существенный ущерб Вашим данным и данным других людей. Поэтому очень важно не передавать свой токен третьим лицам
8. Поле expires_in содержит время жизни токена в секундах. 86400 секунд — это ровно сутки. Через сутки полученный токен перестанет действовать, для продолжения работы нужно будет получить новый по такому же алгоритму

In [3]:
# use your own app id and respective tokens

# скопируйте сюда ваши app_id и access_token, полученные по методу, описанному выше
app_id = '6735892'
access_token = '3c4afdb93c4afdb93c4afdb9923c2c35ad33c4a3c4afdb9679dad4e5f90156bab3ea737'

# id групп ВК Дождя и НТВ
tvrain_id = 17568841
ntv_id = 28658784

In [4]:
# проверка работы API и авторизации пользователя. Если возникает ошибка, то, возможно, access token необходимо обновить
check_id = 1

# api call and test
def vk_get_response(method, parameters, token):
    url = 'https://api.vk.com/method/' + method + '?' + parameters + '&access_token=' + token
#     print url
    return(requests.get(url).json())

answer = vk_get_response(
    'users.get', 'user_ids={0}&v=4.9&lang=ru'.format(check_id), access_token
)['response']
print(answer[0]['first_name'], answer[0]['last_name'])

Павел Дуров


### Получение подписчиков телеканалов НТВ и Дождь в VK

Получим объекты, которые содержат всю информацию о подпиичиках соответствующих групп (указанных в domains) и сохраним их на диск. Получим в итоге два файла - **ntv_subs** и **tvrain_subs** в формате **.pkl** - питоновский формат хранения данных

In [15]:
domains = ['ntv', 'tvrain']


for group_domain in domains:
    offset = 0
    group_id = group_domain
    fields = """sex,bdate,city,country,home_town,lists,domain,has_mobile,
    contacts,connections,education,universities,followers_count,occupation,last_seen,relation"""
    first_sample = vk_get_response(
        'groups.getMembers', 'group_id={0}&offset={1}&fields={2}&v=4.9&lang=ru'.format(
            group_id, offset, fields
        ), token=access_token
    )
    community_count = first_sample['response']['count']
    community_members = []
    for i in range(community_count // 1000 + 1):
        offset = i * 1000
        try:
            answer = vk_get_response(
                'groups.getMembers', 'group_id={0}&offset={1}&fields={2}&v=4.9&lang=ru'.format(
                    group_id, offset, fields), token=access_token
            )
            print("Offset: ", offset)
        except:
            print("Offset: ", offset, " Error")
        community_members += answer['response']['users']
    save_obj(community_members, '{}_subs'.format(group_domain))

Offset:  0
Offset:  1000
Offset:  2000
Offset:  3000
Offset:  4000
Offset:  5000
Offset:  6000
Offset:  7000
Offset:  8000
Offset:  9000
Offset:  10000
Offset:  11000
Offset:  12000
Offset:  13000
Offset:  14000
Offset:  15000
Offset:  16000
Offset:  17000
Offset:  18000
Offset:  19000
Offset:  20000
Offset:  21000
Offset:  22000
Offset:  23000
Offset:  24000
Offset:  25000
Offset:  26000
Offset:  27000
Offset:  28000
Offset:  29000
Offset:  30000
Offset:  31000
Offset:  32000
Offset:  33000
Offset:  34000
Offset:  35000
Offset:  36000
Offset:  37000
Offset:  38000
Offset:  39000
Offset:  40000
Offset:  41000
Offset:  42000
Offset:  43000
Offset:  44000
Offset:  45000
Offset:  46000
Offset:  47000
Offset:  48000
Offset:  49000
Offset:  50000
Offset:  51000
Offset:  52000
Offset:  53000
Offset:  54000
Offset:  55000
Offset:  56000
Offset:  57000
Offset:  58000
Offset:  59000
Offset:  60000
Offset:  61000
Offset:  62000
Offset:  63000
Offset:  64000
Offset:  65000
Offset:  66000
Offset: 

Offset:  167000
Offset:  168000
Offset:  169000
Offset:  170000
Offset:  171000
Offset:  172000
Offset:  173000
Offset:  174000
Offset:  175000
Offset:  176000
Offset:  177000
Offset:  178000
Offset:  179000
Offset:  180000
Offset:  181000
Offset:  182000
Offset:  183000
Offset:  184000
Offset:  185000
Offset:  186000
Offset:  187000
Offset:  188000
Offset:  189000
Offset:  190000
Offset:  191000
Offset:  192000
Offset:  193000
Offset:  194000
Offset:  195000
Offset:  196000
Offset:  197000
Offset:  198000
Offset:  199000
Offset:  200000
Offset:  201000
Offset:  202000
Offset:  203000
Offset:  204000
Offset:  205000
Offset:  206000
Offset:  207000
Offset:  208000
Offset:  209000
Offset:  210000
Offset:  211000
Offset:  212000
Offset:  213000
Offset:  214000
Offset:  215000
Offset:  216000
Offset:  217000
Offset:  218000
Offset:  219000
Offset:  220000
Offset:  221000
Offset:  222000
Offset:  223000
Offset:  224000
Offset:  225000
Offset:  226000
Offset:  227000
Offset:  228000
Offset: 

In [5]:
community_ntv = load_obj('ntv_subs')
community_tvrain = load_obj('tvrain_subs')

In [6]:
community_ntv_df = pd.DataFrame(community_ntv)
community_tvrain_df = pd.DataFrame(community_tvrain)

Сначала получим всех уникальных подписчиков НТВ и Дождя с помощью unique. Далее с помощью numpy.random необходимо выбрать небольшой sample (например, по 1000 из каждой группы) таких людей и объединить их вместе

In [7]:
ntv_uids = community_ntv_df.uid.unique().tolist()
tvrain_uids = community_tvrain_df.uid.unique().tolist()

In [8]:
# получить общий список людей из двух выборок НТВ и Дождя, всего должно быть в итоге около 2000 человек
uids = ntv_uids[0:1000]+tvrain_uids[0:1000]

In [20]:
# получить подписки этих пользователей
print_counter = 0
final_data = []

for uid in uids[:1000]:
    try:
        user_subs = vk_get_response(
            'users.getSubscriptions', 'user_id={0}&v=4.9&lang=ru'.format(int(uid)), access_token
        )
        time.sleep(0.3)
        final_data.append(user_subs)
    except:
        print("Error")
    if print_counter % 100 == 0:
        print("{0} profiles done".format(print_counter))
    print_counter += 1

0 profiles done
100 profiles done
200 profiles done
300 profiles done
400 profiles done
500 profiles done
600 profiles done
700 profiles done
800 profiles done
900 profiles done


In [9]:
final_data = load_obj('final_data')

In [10]:
subs_list = []
groups_freq_dict = {}
top_n = 5

for record, uid in zip(final_data, uids):
    try:
        user_subs = record
        if not user_subs.get('response'):
            user_subs = vk_get_response(
                'users.getSubscriptions', 'user_id={0}&v=4.9&lang=ru'.format(int(uid)), access_token
            )
        subs_pd = pd.DataFrame(
            [
                {
                    'groups_count': user_subs['response']['groups'].get('count'),
                    'groups_list': user_subs['response']['groups'].get('items'),
                    'follows_count':user_subs['response']['users'].get('count'),
                    'follows_list': user_subs['response']['users'].get('items'),
                }
            ]
        )

        for group_id in user_subs['response']['groups'].get('items')[:top_n]:
            if groups_freq_dict.get(group_id):
                groups_freq_dict[group_id] += 1
            else:
                groups_freq_dict[group_id] = 1

        subs_pd['subs_count'] = subs_pd['groups_count'] + subs_pd['follows_count']
        subs_list.append(subs_pd)
    except:
#         print(user_subs)
        pass
    if len(subs_list) % 100 == 0:
        print("Processed {0} users".format(len(subs_list)))

Processed 100 users
Processed 200 users
Processed 300 users
Processed 400 users
Processed 500 users
Processed 600 users
Processed 700 users
Processed 800 users


In [11]:
save_obj(subs_list, 'subs_list')
save_obj(groups_freq_dict, 'groups_freq_dict')

Самые популярные группы

In [12]:
sorted([(key, val) for key, val in groups_freq_dict.items()], key=lambda x: x[1], reverse=True)[:10]

[(28658784, 95),
 (68471405, 78),
 (15755094, 31),
 (24199209, 25),
 (28528027, 24),
 (35531415, 24),
 (75692928, 22),
 (40316705, 21),
 (9494209, 20),
 (460389, 18)]

Загрузка постов со стен групп

In [ ]:
group_doc_dict = {}
counter = 0
groups_freq_dict_top5 = groups_freq_dict

for group_id, freq in groups_freq_dict_top5.items():
    counter += 1
    try:
        check = vk_get_response(
            'wall.get',
            'owner_id={0}&count=100&fields=post_type,marked_as_ads&&v=4.9&lang=ru'.format(int(group_id) * -1),
            access_token
        )
        check = check['response']
        group_doc = ''
        if check[0] != 0:
            for post in check[1:]:
                if post.get('marked_as_ads') != 1:
                    group_doc += post['text']
        group_doc_dict[group_id] = group_doc
    except:
        print("Response error. Group id {0}".format(group_id))
        print(check)
    if counter % 100 == 0:
        print("{0} groups extracted".format(counter))
    time.sleep(0.3)

100 groups extracted
200 groups extracted
300 groups extracted
400 groups extracted
Response error. Group id 87372223
{'error': {'error_code': 15, 'error_msg': 'Access denied: this wall available only for community members', 'request_params': [{'key': 'oauth', 'value': '1'}, {'key': 'method', 'value': 'wall.get'}, {'key': 'owner_id', 'value': '-87372223'}, {'key': 'count', 'value': '100'}, {'key': 'fields', 'value': 'post_type,marked_as_ads'}, {'key': '', 'value': ''}, {'key': 'v', 'value': '4.9'}, {'key': 'lang', 'value': 'ru'}]}}
500 groups extracted
600 groups extracted
700 groups extracted
800 groups extracted
900 groups extracted
1000 groups extracted
1100 groups extracted
Response error. Group id 2009
{'error': {'error_code': 15, 'error_msg': 'Access denied: this wall available only for community members', 'request_params': [{'key': 'oauth', 'value': '1'}, {'key': 'method', 'value': 'wall.get'}, {'key': 'owner_id', 'value': '-2009'}, {'key': 'count', 'value': '100'}, {'key': 'fie

Response error. Group id 25854993
[52374, {'id': 253047, 'from_id': -23044992, 'to_id': -23044992, 'date': 1541479279, 'marked_as_ads': 0, 'post_type': 'post', 'text': '', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -23044992, 'item_id': 466334536, 'thumb_src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 466334536, 'aid': -7, 'owner_id': -23044992, 'user_id': 100, 'src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg', 'src_big': 'https://sun1-12.userapi.com/c540100/v540100601/55f39/Hi2_JvpWci0.jpg', 'src_small': 'https://sun1-16.userapi.com/c540100/v540100601/55f37/ilO5GElsOus.jpg', 'src_xbig': 'https://sun1-18.userapi.com/c540100/v540100601/55f3a/raCG-iljWw8.jpg', 'src_xxbig': 'https://sun1-12.userapi.com/c540100/v540100601/55f3b/TJhpGwNGxUw.jpg', 'width': 768, 'height': 960, 'text': '', 'created': 1541479279, 'post_id': 253047, 'access_key': 'ead73718bc9ac37822'}}], 'pos

Response error. Group id 15199107
[52374, {'id': 253047, 'from_id': -23044992, 'to_id': -23044992, 'date': 1541479279, 'marked_as_ads': 0, 'post_type': 'post', 'text': '', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -23044992, 'item_id': 466334536, 'thumb_src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 466334536, 'aid': -7, 'owner_id': -23044992, 'user_id': 100, 'src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg', 'src_big': 'https://sun1-12.userapi.com/c540100/v540100601/55f39/Hi2_JvpWci0.jpg', 'src_small': 'https://sun1-16.userapi.com/c540100/v540100601/55f37/ilO5GElsOus.jpg', 'src_xbig': 'https://sun1-18.userapi.com/c540100/v540100601/55f3a/raCG-iljWw8.jpg', 'src_xxbig': 'https://sun1-12.userapi.com/c540100/v540100601/55f3b/TJhpGwNGxUw.jpg', 'width': 768, 'height': 960, 'text': '', 'created': 1541479279, 'post_id': 253047, 'access_key': 'ead73718bc9ac37822'}}], 'pos

Response error. Group id 69994406
[52374, {'id': 253047, 'from_id': -23044992, 'to_id': -23044992, 'date': 1541479279, 'marked_as_ads': 0, 'post_type': 'post', 'text': '', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -23044992, 'item_id': 466334536, 'thumb_src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 466334536, 'aid': -7, 'owner_id': -23044992, 'user_id': 100, 'src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg', 'src_big': 'https://sun1-12.userapi.com/c540100/v540100601/55f39/Hi2_JvpWci0.jpg', 'src_small': 'https://sun1-16.userapi.com/c540100/v540100601/55f37/ilO5GElsOus.jpg', 'src_xbig': 'https://sun1-18.userapi.com/c540100/v540100601/55f3a/raCG-iljWw8.jpg', 'src_xxbig': 'https://sun1-12.userapi.com/c540100/v540100601/55f3b/TJhpGwNGxUw.jpg', 'width': 768, 'height': 960, 'text': '', 'created': 1541479279, 'post_id': 253047, 'access_key': 'ead73718bc9ac37822'}}], 'pos

Response error. Group id 85121352
[52374, {'id': 253047, 'from_id': -23044992, 'to_id': -23044992, 'date': 1541479279, 'marked_as_ads': 0, 'post_type': 'post', 'text': '', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -23044992, 'item_id': 466334536, 'thumb_src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 466334536, 'aid': -7, 'owner_id': -23044992, 'user_id': 100, 'src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg', 'src_big': 'https://sun1-12.userapi.com/c540100/v540100601/55f39/Hi2_JvpWci0.jpg', 'src_small': 'https://sun1-16.userapi.com/c540100/v540100601/55f37/ilO5GElsOus.jpg', 'src_xbig': 'https://sun1-18.userapi.com/c540100/v540100601/55f3a/raCG-iljWw8.jpg', 'src_xxbig': 'https://sun1-12.userapi.com/c540100/v540100601/55f3b/TJhpGwNGxUw.jpg', 'width': 768, 'height': 960, 'text': '', 'created': 1541479279, 'post_id': 253047, 'access_key': 'ead73718bc9ac37822'}}], 'pos

...

Response error. Group id 99750523
[52374, {'id': 253047, 'from_id': -23044992, 'to_id': -23044992, 'date': 1541479279, 'marked_as_ads': 0, 'post_type': 'post', 'text': '', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -23044992, 'item_id': 466334536, 'thumb_src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 466334536, 'aid': -7, 'owner_id': -23044992, 'user_id': 100, 'src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg', 'src_big': 'https://sun1-12.userapi.com/c540100/v540100601/55f39/Hi2_JvpWci0.jpg', 'src_small': 'https://sun1-16.userapi.com/c540100/v540100601/55f37/ilO5GElsOus.jpg', 'src_xbig': 'https://sun1-18.userapi.com/c540100/v540100601/55f3a/raCG-iljWw8.jpg', 'src_xxbig': 'https://sun1-12.userapi.com/c540100/v540100601/55f3b/TJhpGwNGxUw.jpg', 'width': 768, 'height': 960, 'text': '', 'created': 1541479279, 'post_id': 253047, 'access_key': 'ead73718bc9ac37822'}}], 'pos

Response error. Group id 32231484
[52374, {'id': 253047, 'from_id': -23044992, 'to_id': -23044992, 'date': 1541479279, 'marked_as_ads': 0, 'post_type': 'post', 'text': '', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -23044992, 'item_id': 466334536, 'thumb_src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 466334536, 'aid': -7, 'owner_id': -23044992, 'user_id': 100, 'src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg', 'src_big': 'https://sun1-12.userapi.com/c540100/v540100601/55f39/Hi2_JvpWci0.jpg', 'src_small': 'https://sun1-16.userapi.com/c540100/v540100601/55f37/ilO5GElsOus.jpg', 'src_xbig': 'https://sun1-18.userapi.com/c540100/v540100601/55f3a/raCG-iljWw8.jpg', 'src_xxbig': 'https://sun1-12.userapi.com/c540100/v540100601/55f3b/TJhpGwNGxUw.jpg', 'width': 768, 'height': 960, 'text': '', 'created': 1541479279, 'post_id': 253047, 'access_key': 'ead73718bc9ac37822'}}], 'pos

Response error. Group id 98382141
[52374, {'id': 253047, 'from_id': -23044992, 'to_id': -23044992, 'date': 1541479279, 'marked_as_ads': 0, 'post_type': 'post', 'text': '', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -23044992, 'item_id': 466334536, 'thumb_src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 466334536, 'aid': -7, 'owner_id': -23044992, 'user_id': 100, 'src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg', 'src_big': 'https://sun1-12.userapi.com/c540100/v540100601/55f39/Hi2_JvpWci0.jpg', 'src_small': 'https://sun1-16.userapi.com/c540100/v540100601/55f37/ilO5GElsOus.jpg', 'src_xbig': 'https://sun1-18.userapi.com/c540100/v540100601/55f3a/raCG-iljWw8.jpg', 'src_xxbig': 'https://sun1-12.userapi.com/c540100/v540100601/55f3b/TJhpGwNGxUw.jpg', 'width': 768, 'height': 960, 'text': '', 'created': 1541479279, 'post_id': 253047, 'access_key': 'ead73718bc9ac37822'}}], 'pos

Response error. Group id 22866546
[52374, {'id': 253047, 'from_id': -23044992, 'to_id': -23044992, 'date': 1541479279, 'marked_as_ads': 0, 'post_type': 'post', 'text': '', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -23044992, 'item_id': 466334536, 'thumb_src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 466334536, 'aid': -7, 'owner_id': -23044992, 'user_id': 100, 'src': 'https://sun1-20.userapi.com/c540100/v540100601/55f38/GoatXsB-v6s.jpg', 'src_big': 'https://sun1-12.userapi.com/c540100/v540100601/55f39/Hi2_JvpWci0.jpg', 'src_small': 'https://sun1-16.userapi.com/c540100/v540100601/55f37/ilO5GElsOus.jpg', 'src_xbig': 'https://sun1-18.userapi.com/c540100/v540100601/55f3a/raCG-iljWw8.jpg', 'src_xxbig': 'https://sun1-12.userapi.com/c540100/v540100601/55f3b/TJhpGwNGxUw.jpg', 'width': 768, 'height': 960, 'text': '', 'created': 1541479279, 'post_id': 253047, 'access_key': 'ead73718bc9ac37822'}}], 'pos

Response error. Group id 27725748
[180160, {'id': 3377450, 'from_id': -39803480, 'to_id': -39803480, 'date': 1541565180, 'marked_as_ads': 0, 'post_type': 'post', 'text': 'Расписание на сегодня:', 'is_pinned': 1, 'media': {'type': 'photo', 'owner_id': -39803480, 'item_id': 456368762, 'thumb_src': 'https://pp.userapi.com/c852232/v852232694/da0/5lLG1TXdChY.jpg'}, 'attachments': [{'type': 'photo', 'photo': {'pid': 456368762, 'aid': -7, 'owner_id': -39803480, 'user_id': 100, 'src': 'https://pp.userapi.com/c852232/v852232694/da0/5lLG1TXdChY.jpg', 'src_big': 'https://pp.userapi.com/c852232/v852232694/da1/AUg3HcrXVJg.jpg', 'src_small': 'https://pp.userapi.com/c852232/v852232694/d9f/4DHeA2JirHE.jpg', 'src_xbig': 'https://pp.userapi.com/c852232/v852232694/da2/Mn8j36DqnOA.jpg', 'src_xxbig': 'https://pp.userapi.com/c852232/v852232694/da3/PoLTl5pnrCM.jpg', 'width': 960, 'height': 960, 'text': '', 'created': 1536762554, 'post_id': 3377450, 'access_key': 'f450ae7d9d3073b6b2'}}], 'post_source': {'type

In [25]:
# сохранить сырые данные по постам групп на диск
save_obj(group_doc_dict, 'group_doc_dict')

In [28]:
# загрузить сохранненые данные
group_doc_dict = load_obj('group_doc_dict')

In [7]:
from bs4 import BeautifulSoup
import re
import string
from nltk import word_tokenize
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
import nltk
from pymorphy2 import MorphAnalyzer

In [5]:
chrs_to_delete = string.punctuation + u'»' + u'«' + u'—' + u'“' + u'„' + u'•' + u'#'
translation_table = {ord(c): None for c in chrs_to_delete if c != u'-'}
units = MorphAnalyzer.DEFAULT_UNITS
morph = MorphAnalyzer(result_type=None, units=units)
PortSt = PorterStemmer()
stopw = set(
    [w for w in stopwords.words(['russian', 'english'])]
    + [u'это', u'году', u'года', u'также', u'етот',
       u'которые', u'который', u'которая', u'поэтому',
       u'весь', u'свой', u'мочь', u'eтот', u'например',
       u'какой-то', u'кто-то', u'самый', u'очень', u'несколько',
       u'источник', u'стать', u'время', u'пока', u'однако',
       u'около', u'немного', u'кроме', u'гораздо', u'каждый',
       u'первый', u'вполне', u'из-за', u'из-под',
       u'второй', u'нужно', u'нужный', u'просто', u'большой',
       u'хороший', u'хотеть', u'начать', u'должный', u'новый', u'день',
       u'метр', u'получить', u'далее', u'именно', u'апрель',
       u'сообщать', u'разный', u'говорить', u'делать',
       u'появиться', u'2016',
       u'2015', u'получить', u'иметь', u'составить', u'дать', u'читать',
       u'ничто', u'достаточно', u'использовать',
       u'принять', u'практически',
       u'находиться', u'месяц', u'достаточно', u'что-то', u'часто',
       u'хотеть', u'начаться', u'делать', u'событие', u'составлять',
       u'остаться', u'заявить', u'сделать', u'дело',
       u'примерно', u'попасть', u'хотя', u'лишь', u'первое',
       u'больший', u'решить', u'число', u'идти', u'давать', u'вопрос',
       u'сегодня', u'часть', u'высокий', u'главный', u'случай', u'место',
       u'конец', u'работать', u'работа', u'слово', u'важный', u'сказать']
)

In [6]:
url_start = 'http[s]?://'
url_end = (
    '(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+'
)
pattern = url_start + url_end

Обработка слов постов групп - трансформация в "хороший" вид. Нормализация и стэмминг, удаление стоп-слов

In [7]:
group_clean_doc_dict = {}
counter = 0

for group_id, doc in group_doc_dict.items():
    soup = BeautifulSoup(doc, 'html.parser')
    body = ' '.join(
        [tag.string.replace('\\n', ' ').replace('\\r', ' ')
         for tag in soup.descendants if tag.string]
    )
    body = re.sub('\[.*?\]','', body)
    body = re.sub(pattern,'', body)
    if body != '':
        body_clean = body.translate(translation_table).lower().strip()
        words = word_tokenize(body_clean)
        tokens = []
        # stemming and text normalization
        for word in words:
            if re.match('^[a-z0-9-]+$', word) is not None:
                tokens.append(PortSt.stem(word))
            elif word.count('-') > 1:
                tokens.append(word)
            else:
                normal_forms = morph.normal_forms(word)
                tokens.append(normal_forms[0] if normal_forms else word)
        # remove stopwords and leave unique words only
        tokens = filter(
            lambda token: token not in stopw, sorted(set(tokens))
        )

        # remove all words with more than 3 chars
        tokens = filter(lambda token: len(token) > 3, tokens)
    else:
        tokens = []
    counter += 1
    if counter % 100 == 0:
        print("{0} docs processed".format(counter))
    group_clean_doc_dict[group_id] = tokens

group_clean_doc_dict = {key: list(val) for key, val in group_clean_doc_dict.items()}

100 docs processed
200 docs processed
300 docs processed
400 docs processed
500 docs processed
600 docs processed
700 docs processed
800 docs processed
900 docs processed
1000 docs processed
1100 docs processed
1200 docs processed
1300 docs processed
1400 docs processed
1500 docs processed
1600 docs processed
1700 docs processed
1800 docs processed
1900 docs processed
2000 docs processed
2100 docs processed
2200 docs processed
2300 docs processed
2400 docs processed
2500 docs processed


In [8]:
# сохранить обработанные данные на диск
save_obj(group_clean_doc_dict, 'group_doc_dict_clean')

In [8]:
group_clean_doc_dict = load_obj('group_doc_dict_clean')

### Обучение LDA модели

In [9]:
from gensim.corpora import TextCorpus
from gensim.models.ldamulticore import LdaMulticore
from gensim.models.ldamodel import LdaModel

class ListTextCorpus(TextCorpus):

    def get_texts(self):
        for doc in self.input:
            yield doc
                
mycorp = ListTextCorpus(input=group_clean_doc_dict.values())
justlda = LdaModel(
    corpus=mycorp, num_topics=20, passes=12
)

In [11]:
print('LdaModel performance')
for i in range(20):
    terms = justlda.get_topic_terms(i)
    print(i, ' '.join(map(lambda x: mycorp.dictionary.get(x[0]), terms)))

LdaModel performance
0 нeдeть любить музыкa пoлучиться жизнь пoчeм тpидцaть тaкoть фигура кoгдa
1 жизнь человек думать знать никто смотреть видеть любить жить понять
2 ингредиент масло соль рецепт вкусный ложка молоко куриный приготовление стакан
3 трокот получении‼ автошторка ￼хороший девушка любить утро повербанк реалистичный домашний
4 сынок область убийство нато умар улыбка город насилие украина приватбанк
5 смотреть пара город русский октябрь музыкальный участие альбом группа получиться
6 фото прекрасный дата добрый ветка декабрь график днём ноябрь 2007
7 жизнь красивый человек интересный новое выходной неделя мастер пройти город
8 район государственный территория площадь город улица октябрь житель культура северный
9 ребро ролик ребёнок отклонить детка самбурский лечение 7350 тебя- хилькевич
10 ждать человек друг новое группа писать смотреть знать фото ноябрь
11 любой образ удобный новое ждать помочь люба цена жизнь рубль
12 человек друг твой семья знать любовь любимый жизнь душа

In [12]:
dummy_dict = {key: 0 for key in range(20)}

group_topics_dict_20 = {
    group_id: dict(list(dummy_dict.items()) + justlda.get_document_topics(mycorp.dictionary.doc2bow(text)))
    for group_id, text in group_clean_doc_dict.items()
}
check_pd_20 = pd.DataFrame.from_dict(group_topics_dict_20, orient='index')
check_pd_20.head(10)
print("Group distribution by the most relevant topic")
pd.Series.round(check_pd_20.idxmax(axis=1).value_counts() * 1. / len(check_pd_20), 2)

Group distribution by the most relevant topic


1     0.31
14    0.26
10    0.09
18    0.05
8     0.05
2     0.05
0     0.03
15    0.02
7     0.02
11    0.02
12    0.02
17    0.02
19    0.02
5     0.01
6     0.01
3     0.01
13    0.01
4     0.01
16    0.01
9     0.01
dtype: float64

In [14]:
check_pd_20.index

Int64Index([       28,        30,        41,        47,        65,        91,
                  223,       272,       337,       439,
            ...
            173025684, 173026085, 173084685, 173192459, 173198725, 173319359,
            173334072, 173397686, 173421457, 173546094],
           dtype='int64', length=2558)

In [12]:
# dump lda model to disk
justlda.save('ldamodel_20_topics')

In [6]:
justlda = load_obj('ldamodel_20_topics')

In [17]:
print("The most typical groups for every topic")
for i in range(20):
    terms = justlda.get_topic_terms(i)
    print(i, ' '.join(map(lambda x: mycorp.dictionary.get(x[0]), terms)))
    typical_groups = check_pd_20[i].sort_values(ascending=False).index[:10]
    for g in typical_groups:
        group_info = vk_get_response(
            'groups.getById', 'group_ids={0}&v=4.9&lang=ru'.format(g), access_token
        )
        print(group_info['response'][0]['name'] + ' ' + 'http://vk.com/club' + str(g))
        time.sleep(0.3)
    print()

The most typical groups for every topic
0 дpaмa жaнp людeть смотреть отпрaвиться серия охoтник выжuть друг дочка
Вопрос времени http://vk.com/club160036323
LOOK AT ME http://vk.com/club51888238
LUXURIOUS LIFE ™ http://vk.com/club39748345
BMW http://vk.com/club15721446
JUST TRAVEL | Мои путешествия http://vk.com/club39651759
Nature|Природа http://vk.com/club35285306
Дорожные Войны http://vk.com/club153344099
Happywear.ru - оптовый интернет-магазин одежды http://vk.com/club107505991
Музыка в машину http://vk.com/club23983339
География в опросах http://vk.com/club73484869

1 рука жить мастеракака вамкак поддержать ремонт лестница подписчик печь aura
Здоровье http://vk.com/club67004747
Стройка - Строительство и Ремонт http://vk.com/club144392420
Моя стройка | Ремонт и строительство http://vk.com/club118600493
FYSM / ФИСМ http://vk.com/club23400027
AliExpress для мужика | Лучшее за день http://vk.com/club145555684
Результаты ЛФЛ СВАО http://vk.com/club171294725
Прораб | Строительство и ремо

Ябвдул 18+ http://vk.com/club50630084
СКУПКА КИНГИСЕПП http://vk.com/club28858039

15 человек думать узнать супер зайти цена мистер клуб играть твой
POSOBIE http://vk.com/club30067066
Прогнозы на спорт | Live от Fuckbet http://vk.com/club54665275
#tech | Умная электроника http://vk.com/club60777940
Aliexpress - Рай для рукоделия http://vk.com/club132645173
Дизайн Ногтей 2018 | Маникюр http://vk.com/club149239818
Тряхни Нормальность http://vk.com/club23433159
E:\Music\Goa Trance, Psy Trance http://vk.com/club134131623
РЕЛЬЕФ /  фитнес / спорт / здоровье / питание http://vk.com/club51211972
Опасное http://vk.com/club151249706
Сурудхои Точики (Таджикская музыка) http://vk.com/club38931597

16 входить пара наверное человек машина пусть прекрасный ненужный полный вечер
Жильё | Прага | Чехия | icizinec http://vk.com/club12913850
Немецкий язык - Start Deutsch http://vk.com/club22628997
Больше, чем фото http://vk.com/club27725748
Кладовая комиксов http://vk.com/club72884889
#КРЫМ http://vk.com

In [1]:
community_ntv_df.head()

NameError: name 'community_ntv_df' is not defined

In [26]:
ntv_uids

[279,
 348,
 510,
 619,
 914,
 985,
 1507,
 1559,
 1642,
 1820,
 2389,
 2395,
 2539,
 2592,
 3450,
 3719,
 4041,
 4566,
 4604,
 4689,
 4731,
 4756,
 4789,
 5028,
 5172,
 5280,
 5466,
 5471,
 5585,
 5805,
 6559,
 6673,
 7012,
 7099,
 7158,
 7179,
 7224,
 7241,
 7347,
 7422,
 7434,
 8157,
 8297,
 8571,
 8910,
 9459,
 9571,
 9651,
 10069,
 10503,
 10932,
 11187,
 12252,
 12394,
 12408,
 12608,
 13008,
 13465,
 13894,
 14065,
 15273,
 15413,
 15505,
 15922,
 15977,
 16552,
 16614,
 17583,
 17666,
 18100,
 18129,
 18429,
 18534,
 19047,
 19304,
 19406,
 19430,
 21267,
 22380,
 22440,
 22566,
 22719,
 24995,
 26835,
 28549,
 29450,
 29990,
 31141,
 32036,
 32287,
 33022,
 33185,
 33339,
 33471,
 34387,
 34483,
 35481,
 36130,
 36252,
 36506,
 36835,
 36903,
 37118,
 38111,
 38536,
 40865,
 40966,
 41135,
 42734,
 45228,
 45426,
 46774,
 46982,
 47540,
 47901,
 48275,
 48904,
 50036,
 50814,
 52059,
 52557,
 52566,
 52975,
 54654,
 57929,
 58095,
 58729,
 60746,
 62060,
 62789,
 63293,
 63485